In [1]:
## 算法 keras 自定义loss  Matlab data
import tensorflow as tf
import numpy as np
from matplotlib import pyplot as plt
import os
import tensorflow_probability as tfp
import scipy.io as scio

# Data size on boundary condition of quasi-potential
Nu=400
dataFile = "xdata1"  
data = scio.loadmat(dataFile)
xdata1 = data['xdata1']
# xdata=tf.reshape(xdata, [Nu, 1])

dataFile = "xdata2"  
data = scio.loadmat(dataFile)
xdata2 = data['xdata2']
# ydata=tf.reshape(ydata, [Nu, 1])

dataFile = "xdata3"  
data = scio.loadmat(dataFile)
xdata3 = data['xdata3']
# Sphi=tf.reshape(Sphi, [Nu, 1])

dataFile = "xdata4"  
data = scio.loadmat(dataFile)
xdata4 = data['xdata4']

dataFile = "xdata5"  
data = scio.loadmat(dataFile)
xdata5 = data['xdata5']

# Data size on Hamiltionian
NH=5000
# DeepNN topology
layers=[2,20,20,20,20,3]
# layers=[2,50,50,20,1]
tf_optimizer = tf.keras.optimizers.Adam(
   learning_rate=0.05,
   beta_1=0.99,
   epsilon=1e-1)
# tf_optimizer = tf.keras.optimizers.SGD

# Jacobi matrix
Jacob=tf.constant([[-2.0,0],[0,-2]])
M=tf.constant([[4.0,0],[0,4]],dtype=tf.float32)
xnode=tf.constant([-1.0,0],dtype=tf.float32)
delta=0.1

xmax=0
xmin=-1.5
ymax=0.6
ymin=-0.6

#### ----------Action plot boundary condition，正式training------------
xdata1 =tf.reduce_sum(xdata1, axis=0)
xdata2 =tf.reduce_sum(xdata2, axis=0)
X_u_train = tf.stack([xdata1,xdata2], axis=1)
xdata3 =tf.reduce_sum(xdata3, axis=0)
xdata4 =tf.reduce_sum(xdata4, axis=0)
xdata5 =tf.reduce_sum(xdata5, axis=0)
u_train=tf.stack([xdata3,xdata4,xdata5], axis=1)
u_train=tf.cast(u_train, dtype=tf.float32)
X_u_train=tf.cast(X_u_train, dtype=tf.float32)
# print(X_u_train)
#### ------------------------------------------------------------------

# sampling points
x=tf.random.uniform([NH],xmin,xmax,dtype=tf.float32)
y=tf.random.uniform([NH],ymin,ymax,dtype=tf.float32)

# # 数据集乱序
# np.random.seed(116)
# np.random.shuffle(x_train)
# np.random.seed(116)
# np.random.shuffle(y_train)
# tf.random.set_seed(116)

class mymodel():
  def __init__(self,layers,optimizer,x,y):
    self.u_model=tf.keras.Sequential()
    self.u_model.add(tf.keras.layers.InputLayer(input_shape=(layers[0],)))
    self.u_model.add(tf.keras.layers.Lambda(
      lambda X: X))
    for width in layers[1:5]:
      self.u_model.add(tf.keras.layers.Dense(
        width, activation=tf.nn.tanh,
        kernel_initializer='glorot_normal'))
        
    self.u_model.add(tf.keras.layers.Dense(
      layers[5], 
      kernel_initializer='glorot_normal'))
        
    # Computing the sizes of weights/biases for future decomposition
    self.sizes_w = []
    self.sizes_b = []
    for i, width in enumerate(layers):
      if i != 1:
        self.sizes_w.append(int(width * layers[1]))
        self.sizes_b.append(int(width if i != 0 else layers[1]))
        
    self.optimizer=optimizer
    self.dtype=tf.float32

  # Defining custom loss
  def __loss(self, u, u_pred, u_pred2):
    H_pred = self.H_model()
    return tf.reduce_mean(tf.square(u[:,0] - u_pred[:,0]),axis=0)  + \
     tf.reduce_mean(tf.square(u[:,1] - u_pred[:,1]),axis=0)  + \
     tf.reduce_mean(tf.square(u[:,2] - u_pred[:,2]),axis=0)  + \
     tf.reduce_mean(tf.square(u_pred2[:,0]),axis=0) * 1 + \
     tf.reduce_mean(tf.square(u_pred2[:,1]),axis=0) * 1 + \
     tf.reduce_mean(tf.square(u_pred2[:,2]),axis=0) * 1 + \
     H_pred * 1
  
  def __grad(self, X, u):
    with tf.GradientTape() as tape:
      Y=self.u_model(X)
      Xnode=tf.constant([-1,0],shape=(1,2),dtype=tf.float32)
      Y2=self.u_model(Xnode)
      loss_value = self.__loss(u, Y, Y2)
    return loss_value, tape.gradient(loss_value, self.__wrap_training_variables())

  def __wrap_training_variables(self):
    var = self.u_model.trainable_variables
    return var
  
  # The actual PINN
  def H_model(self):
    # Using the new GradientTape paradigm of TF2.0,
    # which keeps track of operations to get the gradient at runtime
    with tf.GradientTape(persistent=True) as tape:
      # Watching the two inputs we’ll need later, x and t
      tape.watch(x)
      tape.watch(y)
      # Packing together the inputs
      X_f = tf.stack([x,y], axis=1)

      # Getting the prediction
      u = self.u_model(X_f)
      u0=u[:,2]
    
    # Getting the derivative
    u_x = tape.gradient(u0, x)
    u_y = tape.gradient(u0, y)

    # Letting the tape go
    del tape

    gamma=1
    b1=x-tf.pow(x,3)-gamma*tf.multiply(x,tf.pow(y,2))
    b2=-tf.multiply((1+tf.pow(x,2)),y)
    
    L1=tf.reduce_mean(tf.square(u_x-u[:,0]),axis=0)
    L2=tf.reduce_mean(tf.square(u_y-u[:,1]),axis=0)
    L3=tf.reduce_mean(tf.square(b1*u[:,0]+b2*u[:,1]+0.5*(tf.pow(u[:,0],2)+tf.pow(u[:,1],2))),axis=0)

    # Buidling the Hamiltonian
    return L1+L2+L3

  # def get_weights(self):
  #   w = []
  #   for layer in self.u_model.layers[1:]:
  #     weights_biases = layer.get_weights()
  #     weights = weights_biases[0].flatten()
  #     biases = weights_biases[1]
  #     w.extend(weights)
  #     w.extend(biases)
  #   return tf.convert_to_tensor(w, dtype=self.dtype)

  # def set_weights(self, w):
  #   for i, layer in enumerate(self.u_model.layers[1:]):
  #     start_weights = sum(self.sizes_w[:i]) + sum(self.sizes_b[:i])
  #     end_weights = sum(self.sizes_w[:i+1]) + sum(self.sizes_b[:i])
  #     weights = w[start_weights:end_weights]
  #     w_div = int(self.sizes_w[i] / self.sizes_b[i])
  #     weights = tf.reshape(weights, [w_div, self.sizes_b[i]])
  #     biases = w[end_weights:end_weights + self.sizes_b[i]]
  #     weights_biases = [weights, biases]
  #     layer.set_weights(weights_biases)

  def summary(self):
    return self.u_model.summary()

  # The training function
  def fit(self, X_u, u, tf_epochs=5000):
    # Creating the tensors
    #X_u = tf.convert_to_tensor(X_u, dtype=self.dtype)
    #u = tf.convert_to_tensor(u, dtype=self.dtype)
    #print(self.__wrap_training_variables())

    LOSS=np.zeros([1,tf_epochs])
    for epoch in range(tf_epochs):
      # Optimization step
      loss_value, grads = self.__grad(X_u, u)
      self.optimizer.apply_gradients(zip(grads, self.__wrap_training_variables()))
      LOSS[0,epoch]=loss_value.numpy()
      print('epoch, loss_value:', epoch, loss_value)

    scio.savemat('LOSS.mat',{'LOSS':LOSS})
    # def loss_and_flat_grad(w):
    #   with tf.GradientTape() as tape:
    #     self.set_weights(w)
    #     Xnode=tf.constant([-1,0],shape=(1,2),dtype=tf.float32)
    #     Y2=tf.reduce_sum(self.u_model(Xnode),axis=1)
    #     loss_value = self.__loss(u, self.u_model(X_u), Y2)
    #   grad = tape.gradient(loss_value, self.u_model.trainable_variables)
    #   grad_flat = []
    #   for g in grad:
    #     grad_flat.append(tf.reshape(g, [-1]))
    #   grad_flat =  tf.concat(grad_flat, 0)
    #   return loss_value, grad_flat

    # tfp.optimizer.lbfgs_minimize(
    #   loss_and_flat_grad,
    #   initial_position=self.get_weights(),
    #   num_correction_pairs=50,
    #   max_iterations=2000)
    # lbfgs(loss_and_flat_grad,
    #   self.get_weights())
    # lbfgs(loss_and_flat_grad,
    #   self.get_weights(),
    #   nt_config, Struct(), True,
    #   lambda epoch, loss, is_iter:
    #     self.logger.log_train_epoch(epoch, loss, "", is_iter))

    # print(self.__wrap_training_variables())

  def predict(self, X_star):
    u_star = self.u_model(X_star)
    # f_star = self.H_model()
    return u_star#, f_star


model=mymodel(layers, tf_optimizer, x, y)

# checkpoint_save_path="./checkpoint/mnist.ckpt"
# if os.path.exists(checkpoint_save_path + '.index'):
#   print('-------------------load the model---------------------')
#   model.load_weights(checkpoint_save_path)

# cp_callback=tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_save_path,
#                         save_weights_only=True,
#                         save_best_only=True)

history=model.fit(X_u_train, u_train, tf_epochs=50000)

model.summary()

# Getting the model predictions, from the same (x,t) that the predictions were previously gotten from
x1=tf.constant([-1.5,-1.5,-1.5,-1,-1,-1,0,0,0],dtype=tf.float32)
y1=tf.constant([-0.6,0,0.6,-0.6,0,0.6,-0.6,0,0.6],dtype=tf.float32)
X_star = tf.stack([x1,y1], axis=1)
print('X_star:\n ', X_star)
u_pred= model.predict(X_star)
print('u_pred:\n ', u_pred)

dataFile = "xtest1"  
data = scio.loadmat(dataFile)
xtest1 = data['xtest1']
dataFile = "xtest2"  
data = scio.loadmat(dataFile)
xtest2 = data['xtest2']
xtest1 =tf.reduce_sum(xtest1, axis=0)
xtest2 =tf.reduce_sum(xtest2, axis=0)
X_star = tf.stack([xtest1,xtest2], axis=1)
Stest= model.predict(X_star)
scio.savemat('Stest.mat',{'Stest':Stest.numpy()})


epoch, loss_value: 0 tf.Tensor(4.3980765, shape=(), dtype=float32)
epoch, loss_value: 1 tf.Tensor(3.165173, shape=(), dtype=float32)
epoch, loss_value: 2 tf.Tensor(3.629121, shape=(), dtype=float32)
epoch, loss_value: 3 tf.Tensor(3.457651, shape=(), dtype=float32)
epoch, loss_value: 4 tf.Tensor(3.0659466, shape=(), dtype=float32)
epoch, loss_value: 5 tf.Tensor(2.8694823, shape=(), dtype=float32)
epoch, loss_value: 6 tf.Tensor(2.836184, shape=(), dtype=float32)
epoch, loss_value: 7 tf.Tensor(2.8493242, shape=(), dtype=float32)
epoch, loss_value: 8 tf.Tensor(2.8637102, shape=(), dtype=float32)
epoch, loss_value: 9 tf.Tensor(2.860015, shape=(), dtype=float32)
epoch, loss_value: 10 tf.Tensor(2.810382, shape=(), dtype=float32)
epoch, loss_value: 11 tf.Tensor(2.7056608, shape=(), dtype=float32)
epoch, loss_value: 12 tf.Tensor(2.575817, shape=(), dtype=float32)
epoch, loss_value: 13 tf.Tensor(2.473538, shape=(), dtype=float32)
epoch, loss_value: 14 tf.Tensor(2.440824, shape=(), dtype=float32)

In [1]:
# Compute MPEP
h=0.005
nT=10000
x1=np.zeros(nT,)
x2=np.zeros(nT,)
x1[1]=-0.01
x2[1]=0.01
for epoch in range(nT-2):
    x01=tf.constant(x1[epoch+1],shape=(1,),dtype=tf.float32)
    x02=tf.constant(x2[epoch+1],shape=(1,),dtype=tf.float32)
    x0= tf.stack([x01,x02],axis=1)
    p=model.predict(x0)
    p =tf.reduce_sum(p, axis=0)
    p1=p.numpy()
    gamma=1.0
    x1[epoch+2]=x1[epoch+1] -h * (x1[epoch+1]-np.power(x1[epoch+1],3)-gamma*x1[epoch+1]*np.power(x2[epoch+1],2)+p1[0])
    x2[epoch+2]=x2[epoch+1] -h * (-(1+np.power(x1[epoch+1],2))*x2[epoch+1]+p1[1])

MPEP=tf.stack([x1,x2], axis=1)
scio.savemat('MPEP.mat',{'MPEP':MPEP.numpy()})

NameError: name 'np' is not defined

In [2]:
# Compute controlled MFPT
h=0.001
nT=10000000000
Npath=1000
N=0
FPT=np.zeros(Npath,)
xmax=0
D=0.05
gamma=1.0
cd=0.2035
x1=-1.0*np.ones(Npath,)
x2=np.zeros(Npath,)
for epoch in range(nT):
    n=x1.size
    x01=tf.constant(x1,shape=(n,),dtype=tf.float32)
    x02=tf.constant(x2,shape=(n,),dtype=tf.float32)
    x0= tf.stack([x01,x02],axis=1)
    p=model.predict(x0)
    p1=p.numpy()
    x3=x1 +h * (x1-np.power(x1,3)-gamma*x1*np.power(x2,2)+cd*p1[:,0]) +np.sqrt(D*h)*np.random.normal(size=(n,))
    x4=x2 +h * (-(1+np.power(x1,2))*x2+cd*p1[:,1]) +np.sqrt(D*h)*np.random.normal(size=(n,))
    
    I=x3>xmax
    n0=x3[I].size
    if n0>0:
        FPT[N:N+n0]=epoch*h
        x3=x3[~I]
        x4=x4[~I]
        N=N+n0
        print(epoch,x3.size)
        
    if x3.size==0:
        break
    x1=x3
    x2=x4

MFPT=np.sum(FPT)/Npath
print(FPT)
print(MFPT)
scio.savemat('FPT.mat',{'FPT':FPT})

5172 999
5902 998
13526 997
15675 996
18472 995
20614 994
20780 993
20816 992
20963 991
21219 990
22328 989
23845 988
24832 987
26239 986
27816 985
29130 984
32348 983
33056 982
33399 981
34825 980
35390 979
36837 978
38698 977
41094 976
42349 975
43167 974
43544 973
44245 972
45399 971
45711 970
48641 969
49385 968
49654 967
51230 966
51984 965
52655 964
55617 963
56242 962
56421 961
57334 960
57410 959
57629 958
58479 957
59314 956
60455 955
62326 954
64639 953
65193 952
65287 951
67985 950
68036 949
71883 948
72818 947
74090 946
74663 945
74718 944
76799 943
77148 942
79546 941
79673 940
80405 939
80999 938
81890 937
82867 936
83469 935
84363 934
84672 933
85704 932
85788 931
89256 930
89279 929
89408 928
91049 927
92060 926
95175 925
98475 924
99963 923
100159 922
100407 921
101095 920
102870 919
103945 918
105457 917
105858 916
106868 915
108551 914
108594 913
108776 912
109326 911
114888 910
118204 909
118318 908
118497 907
120225 906
120922 905
121034 904
122475 903
126963 902
1